![](https://upload.wikimedia.org/wikipedia/de/thumb/7/7b/Ix_logo.svg/232px-Ix_logo.svg.png) 
# AskYourBooks Prototyp

## Installation der nötigen Bibliotheken

In [1]:
!python --version

Python 3.10.11


In [2]:
!pip -q install gradio
!pip -q install langchain
!pip -q install llama-cpp-python
!pip -q install transformers
!pip -q install sentence_transformers
!pip -q install tiktoken
!pip -q install faiss-cpu


     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 17.4/17.4 MB 38.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.0/1.0 MB 28.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 57.0/57.0 kB 4.2 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 288.1/288.1 kB 24.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 75.4/75.4 kB 7.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 224.5/224.5 kB 21.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 50.5/50.5 kB 4.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 137.2/137.2 kB 4.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 45.7/45.7 kB 3.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 58.3/58.3 kB 3.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 129.9/129.9 kB 918.4 kB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 58.3/58.3 kB 1.2 MB/s eta 0:0

In [3]:
!git lfs install --skip-repo

Git LFS initialized.


## Import der nötigen Python Module

In [4]:
import os
import requests
import io
import random
import time
from getpass import getpass
from langchain import HuggingFaceHub
from langchain.embeddings import HuggingFaceEmbeddings
from langchain.text_splitter import TokenTextSplitter, CharacterTextSplitter
from langchain import PromptTemplate, LLMChain
from langchain.chains.question_answering import load_qa_chain
from langchain.vectorstores import FAISS
from langchain.document_loaders import TextLoader
from langchain.callbacks.manager import CallbackManager
from langchain.callbacks.streaming_stdout import StreamingStdOutCallbackHandler
from langchain.llms import LlamaCpp

## Wichtige Konstanten

In [5]:
# Enter your Hugging Face API Token here
os.environ["HUGGINGFACEHUB_API_TOKEN"] = getpass()
REPO_ID = "declare-lab/flan-alpaca-large"
#REPO_ID = "decapoda-research/llama-7b-hf"
TEXT_URL = "https://www.gutenberg.org/cache/epub/164/pg164.txt"


··········


## Sprachmodell und Embeddings initialisieren

In [6]:
llm = HuggingFaceHub(repo_id=REPO_ID, model_kwargs={"temperature":0, "max_length":512})

In [7]:
embeddings = HuggingFaceEmbeddings()

In [8]:
callback_manager = CallbackManager([StreamingStdOutCallbackHandler()])

In [9]:
chain = load_qa_chain(llm, chain_type="stuff", verbose=False)

## Text einlesen und verarbeiten

In [10]:
# Get text
res = requests.get(TEXT_URL)
with open("pg164.txt", "w") as f:
  f.write(res.text)

In [11]:
# Load and split text
loader = TextLoader("./pg164.txt")
documents = loader.load()
text_splitter = CharacterTextSplitter(chunk_size=1000, chunk_overlap=10)
docs = text_splitter.split_documents(documents)

## Embedings erzeugen und in Vektordatenbank speichern

In [12]:
db = FAISS.from_documents(docs, embeddings)

In [13]:
db.save_local(folder_path=".", index_name="faiss_index")

## Fragen an den Text

In [14]:
question = "What is the name of the captain of the Nautilus"
relevant_docs = db.similarity_search(question)
chain.run(input_documents=relevant_docs, question=question, raw_response=True, callbacks=callback_manager)

'Captain Nemo.'

In [15]:
question = "What are the names of the crew members of the Nautilus?"
relevant_docs = db.similarity_search(question)
chain.run(input_documents=relevant_docs, question=question, raw_response=True, callbacks=callback_manager)

'Captain Nemo, Conseil, and the Canadian.'

In [16]:
question = "What is the name of the Canadian?"
relevant_docs = db.similarity_search(question)
chain.run(input_documents=relevant_docs, question=question, raw_response=True, callbacks=callback_manager)

'Ned Land.'

In [19]:
question = "What musical instrument does Captain Nemo play?"
relevant_docs = db.similarity_search(question)
chain.run(input_documents=relevant_docs, question=question, raw_response=True, callbacks=callback_manager)

'Captain Nemo plays the organ.'

In [20]:
question = "What is the name of Professor Aronnax's butler?"
relevant_docs = db.similarity_search(question)
chain.run(input_documents=relevant_docs, question=question, raw_response=True, callbacks=callback_manager)

'Conseil.'

In [25]:
question = "In which areas was the Nautilus traveling?"
relevant_docs = db.similarity_search(question)
chain.run(input_documents=relevant_docs, question=question, raw_response=True, callbacks=callback_manager)

'The Nautilus was traveling in the Indian Ocean.'

In [26]:
question = "Why doesn't Captain Nemo like people?"
relevant_docs = db.similarity_search(question)
chain.run(input_documents=relevant_docs, question=question, raw_response=True, callbacks=callback_manager)

"No, Captain Nemo doesn't like people because he is not satisfied with shunning man."

## Gradio Anwendung

In [27]:
import gradio as gr

In [28]:
question_examples = [
    "What is the name of the captain of the Nautilus?",
    "What are the names of the crew members of the Nautilus?",
    "What is the name of the Canadian?",
    "What is Ned Land's profession?",
    "What musical instrument does Captain Nemo play?",
    "What is the name of Professor Aronnax's butler?",
    "In which areas was the Nautilus traveling?",
    "Why doesn't Captain Nemo hate the society?"
]

In [29]:
def read_textfile(File):
  loader = TextLoader(File.name)
  documents = loader.load()
  text_splitter = CharacterTextSplitter(chunk_size=1000, chunk_overlap=10)
  docs = text_splitter.split_documents(documents)
  db = FAISS.from_documents(docs, embeddings)
  db.save_local(folder_path=".", index_name="faiss_index")

In [30]:
def ask_question(question, chat_history):
  llm = HuggingFaceHub(repo_id=REPO_ID, model_kwargs={"temperature":0, "max_length":512})
  embeddings = HuggingFaceEmbeddings()
  chain = load_qa_chain(llm, chain_type="stuff", verbose=False)
  db = FAISS.load_local(".", embeddings, index_name="faiss_index")
  relevant_docs = db.similarity_search(question)
  
  answer = chain.run(
      input_documents=relevant_docs, 
      question=question, 
      callbacks=callback_manager
  )

  chat_history.append((question, answer))
  time.sleep(1)
  return "", chat_history

In [31]:
with gr.Blocks() as demo:
  gr.Markdown("## 📚AskYourBooks")
  gr.Markdown("""
    Ask questions to your books in txt format. After a short indexing time, 
    ask questions about the content of the book.
    """
  )
  textfile = gr.File(label="Drag your book here")
  ask_textbox = gr.Textbox(label="Question")
  sample_questions = gr.Examples(examples=question_examples, inputs=[ask_textbox])
  ask_button = gr.Button("Ask your book")
  clear_button = gr.Button("Clear chat")
  chatbot = gr.Chatbot(label="Conversation")
  
  textfile.change(fn=read_textfile, inputs=[textfile], outputs=[])
  ask_button.click(
      fn=ask_question, 
      inputs=[ask_textbox, chatbot], 
      outputs=[ask_textbox, chatbot]
  )
  clear_button.click(lambda: None, None, chatbot, queue=False)
  

In [32]:
demo.launch(debug=True)

Colab notebook detected. This cell will run indefinitely so that you can see errors and logs. To turn off, set debug=False in launch().
Note: opening Chrome Inspector may crash demo inside Colab notebooks.

To create a public link, set `share=True` in `launch()`.


<IPython.core.display.Javascript object>

Keyboard interruption in main thread... closing server.
